Imports

In [1]:
import torch
import os
import sys
from torchvision import transforms
from IPython.display import Image 
import progressbar


script_root_dir = '../'
if script_root_dir not in sys.path:
    sys.path.append(script_root_dir)
    
from train import dataLoader
from train.configParser import ConfigParser
from myhelpers.color_PCA import Color_PCA
from myhelpers import TrialStatistics

Parameters

In [2]:
experimentsPath="/home/elhamod/HGNN/experiments/"
experimentName="DifferentResolutions"
experimentHash="1e1fb23ee91b9ce31e8f09e5635e8950c1fe5ba74983b13f7d6483bc"
dataPath="/data/BGNN_data/"

applyHorizontalFlip = True
applyHorizontalFlipProbability = 0.3

applyTranslation=True
applyTranslationAmount = 0.25

applyColorPCA=True
colorPCAperturbationMagnitude = 0.1

numOfAugmentedVersions = 30

cuda = 7

In [3]:
# set cuda
if torch.cuda.is_available():
    torch.cuda.set_device(cuda)
    print("using cuda", cuda)

using cuda 7


Load dataset

In [4]:
# Get experiment params.
config_parser = ConfigParser(experimentsPath, dataPath, experimentName)
experiment_params = None
for params_ in config_parser.getExperiments():
    if experimentHash == TrialStatistics.getTrialName(params_):
        experiment_params = params_
        break
if experiment_params is None:
    print("Could not find experiment!", experimentHash)
    raise
    
imageDimension = experiment_params["img_res"] if experiment_params["img_res"] is not None else 224
print('imageDimension = ', imageDimension)

# Get the dataset
experimentPathAndName = os.path.join(experimentsPath, experimentName)
datasetManager = dataLoader.datasetManager(experimentPathAndName)
datasetManager.updateParams(config_parser.fixPaths({**experiment_params, **{"img_res": None}}))
dataset = datasetManager.getDataset()
dataset.imageDimension = imageDimension
# datasetManager.updateParams(config_parser.fixPaths(experiment_params))
# dataset_compressed = datasetManager.getDataset()

# disable normalization before augmentation.
dataset.toggle_image_loading(augmentation=False, normalization=False)

# Create appropriate loaders
loaderPerImage = torch.utils.data.DataLoader(dataset, batch_size=1)
datasetSize = len(dataset)
loaderAllImages = torch.utils.data.DataLoader(dataset, batch_size=datasetSize)
print("number of images", datasetSize)

imageDimension =  448
Creating dataset...


Loading images: 100%|██████████| 2600/2600 [02:22<00:00, 18.25it/s, fileName=/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588.jpg]  

Creating dataset... Done.
number of images 2600


Generate data

In [5]:
color_pca = Color_PCA(loaderAllImages, colorPCAperturbationMagnitude)

with progressbar.ProgressBar(max_value=datasetSize) as bar:
    k=1
    for batch in loaderPerImage:
        original = batch['image'].squeeze()
        fileName = batch['fileName'][0]
        prefix, ext = os.path.splitext(fileName)

        if torch.cuda.is_available():
            original = original.cpu()
        
        # Generate a scaled version
        savedFileName = os.path.join(dataset.csv_processor.get_image_full_path(), prefix+"_"+str(imageDimension)+ext)
        scaled = transforms.ToPILImage()(original)
        scaled.save(savedFileName)
        print(savedFileName, "saved!")

        # Generate augmented versions
        for j in range(numOfAugmentedVersions):
            image = transforms.ToPILImage()(original)

            if applyHorizontalFlip:
                image = transforms.RandomHorizontalFlip(p=applyHorizontalFlipProbability)(image)
    #             display(image)

            if applyTranslation:
                RGBmean = (int(0.485*255), int(0.456*255), int(0.406*255))
                image = transforms.RandomAffine(degrees=0, translate=(applyTranslationAmount,
                                                                      applyTranslationAmount),
                                               fillcolor=RGBmean)(image)
    #             display(image)

            if applyColorPCA:
                image = transforms.ToTensor()(image).unsqueeze(0)
                image = transforms.Lambda(color_pca.perturb_color)(image).type(torch.float32) 

                image = transforms.ToPILImage()(image.squeeze())
    #             display(image)


            savedFileName = os.path.join(dataset.csv_processor.get_image_full_path(), prefix+"_"+str(imageDimension)+"_aug"+str(j)+ext)
            image.save(savedFileName)
            print(savedFileName, "saved!")
            
        bar.update(k)
        k = k + 1

    
    

Transforming images: 100%|██████████| 2600/2600 [01:06<00:00, 39.16it/s]


/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug0.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug1.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug2.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug3.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug4.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug5.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug6.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug7.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug8.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug9.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug10.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug11.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_4

N/A% (0 of 2600) |                       | Elapsed Time: 0:00:00 ETA:  --:--:--

/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug25.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug26.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug27.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug28.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_107563_448_aug29.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_46357_448.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_46357_448_aug0.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_46357_448_aug1.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_46357_448_aug2.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_46357_448_aug3.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_46357_448_aug4.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_46357_448_aug5.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_46357_448_aug6.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_46357_448_aug

  0% (2 of 2600) |                       | Elapsed Time: 0:00:00 ETA:   0:09:27

...

/data/BGNN_data/INHS_cropped/images/INHS_FISH_26288_448_aug24.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_26288_448_aug25.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_26288_448_aug26.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_26288_448_aug27.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_26288_448_aug28.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_26288_448_aug29.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug0.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug1.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug2.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug3.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug4.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug5.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug6.jp

 99% (2599 of 2600) |################### | Elapsed Time: 0:22:59 ETA:   0:00:00

/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug25.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug26.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug27.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug28.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_92277_448_aug29.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug0.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug1.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug2.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug3.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug4.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug5.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug6.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug7.jpg

100% (2600 of 2600) |####################| Elapsed Time: 0:23:00 Time:  0:23:00


/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug18.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug19.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug20.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug21.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug22.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug23.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug24.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug25.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug26.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug27.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug28.jpg saved!
/data/BGNN_data/INHS_cropped/images/INHS_FISH_63588_448_aug29.jpg saved!
